In [36]:
import pandas as pd
import pyodbc
import plotly.graph_objs as go
from plotly.subplots import make_subplots

# Warnings y estilos
import warnings
warnings.filterwarnings('ignore')

# Para notebooks (opcional)
%matplotlib inline

# Conexión a SQL Server
conn_str = (
    "DRIVER={ODBC Driver 17 for SQL Server};"
    "SERVER=localhost,1433;"
    "DATABASE=FlujoVehicular;"
    "UID=sa;"
    "PWD=StrongPassw0rd!;"
)
conn = pyodbc.connect(conn_str)

# --- 1. Datos reales desde 2017
query_real = """
SELECT 
    CONVERT(DATETIME, CONVERT(VARCHAR, f.fecha, 23) + ' ' + RIGHT('0' + CAST(h.hora_id AS VARCHAR), 2) + ':00') AS date_time,
    f.cantidad_pasos
FROM fact_pasos f
INNER JOIN dim_hora h ON f.hora_id = h.hora_id
"""
df_real = pd.read_sql(query_real, conn)
df_real['date_time'] = pd.to_datetime(df_real['date_time'])

# --- 2. Forecasting 2020 (estimación sin pandemia)
df_forecast = pd.read_sql("SELECT * FROM vw_forecasting_pasos", conn)
df_forecast['date_time'] = pd.to_datetime(df_forecast['fecha_id'], format='%Y%m%d') + \
                           pd.to_timedelta(df_forecast['hora_id'], unit='h')
df_forecast = df_forecast[df_forecast['date_time'].dt.year == 2020]

# --- 3. Predicción futura 2021+
df_pred = pd.read_sql("SELECT * FROM vw_prediccion_pasos", conn)
df_pred['date_time'] = pd.to_datetime(df_pred['id_prediccion'].str[:8], format='%Y%m%d') + \
                       pd.to_timedelta(df_pred['id_prediccion'].str[8:].astype(int), unit='h')

# --- Cargar ambas vistas
df_fact = pd.read_sql("SELECT fecha, hora_id, cantidad_pasos FROM vw_fact_pasos", conn)
df_forecasting = pd.read_sql("SELECT date_time, cantidad_pasos FROM vw_fact_pasos_forecasting", conn)

conn.close()

# --- Agrupación correcta por hora (SUM, no promedio)
df_real_grouped = df_real.groupby('date_time', as_index=False)['cantidad_pasos'].sum()

df_forecast_grouped = df_forecast.groupby('date_time', as_index=False)[
    ['MODEL_EXOGENEAS_XGB', 'MODEL_EXOGENEAS_LGBM', 'MODEL_EXOGENEAS_CatBoost']
].sum()

df_pred_grouped = df_pred.groupby('date_time', as_index=False)[
    ['MODEL_EXOGENEAS_XGB', 'MODEL_EXOGENEAS_LGBM', 'MODEL_EXOGENEAS_CatBoost']
].sum()

# Calcular totales por modelo
df_totales = pd.DataFrame({
    'Modelo': ['Real', 'Forecast XGB', 'Forecast LGBM', 'Forecast CatBoost',
               'Predicción XGB', 'Predicción LGBM', 'Predicción CatBoost'],
    'Total Pasos': [
        df_real_grouped['cantidad_pasos'].sum(),
        df_forecast_grouped['MODEL_EXOGENEAS_XGB'].sum(),
        df_forecast_grouped['MODEL_EXOGENEAS_LGBM'].sum(),
        df_forecast_grouped['MODEL_EXOGENEAS_CatBoost'].sum(),
        df_pred_grouped['MODEL_EXOGENEAS_XGB'].sum(),
        df_pred_grouped['MODEL_EXOGENEAS_LGBM'].sum(),
        df_pred_grouped['MODEL_EXOGENEAS_CatBoost'].sum()
    ]
})

from plotly.subplots import make_subplots
import plotly.graph_objs as go

# Crear subgráfico: gráfico a la izquierda y tabla a la derecha
fig = make_subplots(
    rows=1, cols=2,
    column_widths=[0.75, 0.25],
    specs=[[{"type": "xy"}, {"type": "table"}]]
)

# --- Serie real
fig.add_trace(go.Scatter(
    x=df_real_grouped['date_time'],
    y=df_real_grouped['cantidad_pasos'],
    mode='lines',
    name='Real',
    line=dict(color='black')
), row=1, col=1)

# --- Forecast (2020)
fig.add_trace(go.Scatter(
    x=df_forecast_grouped['date_time'],
    y=df_forecast_grouped['MODEL_EXOGENEAS_XGB'],
    mode='lines',
    name='Forecast XGB',
    line=dict(dash='dash', color='blue')
), row=1, col=1)

fig.add_trace(go.Scatter(
    x=df_forecast_grouped['date_time'],
    y=df_forecast_grouped['MODEL_EXOGENEAS_LGBM'],
    mode='lines',
    name='Forecast LGBM',
    line=dict(dash='dash', color='orange')
), row=1, col=1)

fig.add_trace(go.Scatter(
    x=df_forecast_grouped['date_time'],
    y=df_forecast_grouped['MODEL_EXOGENEAS_CatBoost'],
    mode='lines',
    name='Forecast CatBoost',
    line=dict(dash='dash', color='purple')
), row=1, col=1)

# --- Predicciones (2021+)
fig.add_trace(go.Scatter(
    x=df_pred_grouped['date_time'],
    y=df_pred_grouped['MODEL_EXOGENEAS_XGB'],
    mode='lines',
    name='Predicción XGB',
    line=dict(dash='dot', color='blue')
), row=1, col=1)

fig.add_trace(go.Scatter(
    x=df_pred_grouped['date_time'],
    y=df_pred_grouped['MODEL_EXOGENEAS_LGBM'],
    mode='lines',
    name='Predicción LGBM',
    line=dict(dash='dot', color='orange')
), row=1, col=1)

fig.add_trace(go.Scatter(
    x=df_pred_grouped['date_time'],
    y=df_pred_grouped['MODEL_EXOGENEAS_CatBoost'],
    mode='lines',
    name='Predicción CatBoost',
    line=dict(dash='dot', color='purple')
), row=1, col=1)

# --- Tabla de totales
fig.add_trace(go.Table(
    header=dict(
        values=['Modelo', 'Total Pasos'],
        fill_color='paleturquoise',
        align='left'
    ),
    cells=dict(
        values=[
            df_totales['Modelo'],
            df_totales['Total Pasos'].round(0)
        ],
        fill_color='lavender',
        align='left'
    )
), row=1, col=2)

# --- Layout
fig.update_layout(
    title='Flujo vehicular: Real vs Estimaciones vs Predicciones',
    template='plotly_white',
    width=1400,
    height=650,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=-0.35,
        xanchor="left",
        x=0
    ),
    xaxis=dict(
        title='Fecha y hora',
        rangeselector=dict(
            buttons=list([
                dict(count=1, label="1d", step="day", stepmode="backward"),
                dict(count=7, label="1w", step="day", stepmode="backward"),
                dict(count=1, label="1m", step="month", stepmode="backward"),
                dict(count=6, label="6m", step="month", stepmode="backward"),
                dict(step="all", label="Todo")
            ])
        ),
        rangeslider=dict(visible=True),
        type="date"
    ),
    yaxis=dict(title="Cantidad de pasos por hora")
)

fig.show()


In [37]:
# --- Crear columna datetime para fact
df_fact['date_time'] = pd.to_datetime(df_fact['fecha'].astype(str)) + pd.to_timedelta(df_fact['hora_id'], unit='h')

# --- Agrupar por datetime (acumulado por hora)
fact_grouped = df_fact.groupby('date_time', as_index=False)['cantidad_pasos'].sum()
forecasting_grouped = df_forecasting.groupby('date_time', as_index=False)['cantidad_pasos'].sum()

# --- Gráfico interactivo
fig = make_subplots(rows=1, cols=1)

fig.add_trace(go.Scatter(
    x=fact_grouped['date_time'],
    y=fact_grouped['cantidad_pasos'],
    mode='lines',
    name='Pasos reales (vw_fact_pasos)'
))

fig.add_trace(go.Scatter(
    x=forecasting_grouped['date_time'],
    y=forecasting_grouped['cantidad_pasos'],
    mode='lines',
    name='Pasos reales (vw_fact_pasos_forecasting)'
))

fig.update_layout(
    title='Comparación de vistas fact_pasos vs fact_pasos_forecasting',
    xaxis_title='Fecha y hora',
    yaxis_title='Cantidad de pasos',
    height=500
)

fig.show()